## Configuration

In [12]:
import pickle

def load_embed(path, set_name):
    path = path + "/" + set_name + "_transe_embed.pkl"
    print("Load embedding:", path)
    embed = pickle.load(open(path, "rb"))
    return embed

def load_kg(path, set_name):
    kg_file = path + "/" + set_name + "_kg.pkl"
    print("Load KG:", kg_file)
    kg = pickle.load(open(kg_file, "rb"))
    return kg

def load_dataset(path, set_name):
    dataset_file = path + "/" + set_name + "_dataset.pkl"
    dataset_obj = pickle.load(open(dataset_file, "rb"))
    return dataset_obj

def load_embed(path, set_name):
    path = path + "/" + set_name + "_transe_embed.pkl"
    print("Load embedding:", path)
    embed = pickle.load(open(path, "rb"))
    return embed

path="../../data/cell_phones/Amazon_Cellphones_01_01"
set_name="train"
embeds = load_embed(path, set_name)
embeds['user'].shape #(27879, 100)

Load embedding: ../../data/cell_phones/Amazon_Cellphones_01_01/train_transe_embed.pkl


(27879, 100)

In [13]:
from easydict import EasyDict as edict
import json
from copy import deepcopy
from utils import *
import numpy as np

class Agrument:
    config = '../../config/cell_phones/graph_reasoning/UPGPR_feature.json'
    
args = Agrument()

with open(args.config, "r") as f:
    config = edict(json.load(f))
    
config.processed_data_dir = '../../data/cell_phones/Amazon_Cellphones_01_01/'
set_name = "train"
dataset = load_dataset(config.processed_data_dir, set_name)

# load cold start users
cold_users_path = os.path.join(config.processed_data_dir, "cold_start_users.json")
cold_users = json.load(open(cold_users_path, "r"))

# set all cold start users embeddings to 0
tmp_cold_users = cold_users['train'] #cold_users["test"] + cold_users["validation"]
# len(users) 22302
embeds["user"][tmp_cold_users] = 0

transe_config = config.TRAIN_EMBEDS
transe_config["cold_start_embeddings"] = "avg"

In [14]:
# dataset.data_args.user_relation.items()
# dict_items([('mentioned', ['mentioned_by_u_w.txt', 'word']), ('interested_in', ['interested_in_u_c.txt', 'category']), ('like', ['like_u_b.txt', 'brand'])])

## User-Preferred

In [26]:
set_user_acc_feature = [979]
set_user_rej_feature = [1042, 1032, 992, 973, 1062, 1031, 991, 969, 990]
set_user_rej_items = []

## Translation

In [28]:
# dataset

In [24]:
dataset.data_args.user_relation.items()

dict_items([('mentioned', ['mentioned_by_u_w.txt', 'word']), ('interested_in', ['interested_in_u_c.txt', 'category']), ('like', ['like_u_b.txt', 'brand'])])

In [ ]:
# key : value => entity : relation
relations = { 
    'feature': [
        {'set_user_acc_feature' : ['interested_in', 'like']}, 
        {'set_user_rej_feature' : ['disintereseted_in', 'dislike']}
    ],
    'item' : [
        {'set_user_rej_items' : ['non-purchase']}
    ]
}
# Note i dont have 'disintereseted_in', 'dislike', 'non-purchase'

In [29]:
def translation(embeds, dataset):
    users = cold_users['train']
    # making a copy of the embeddings to avoid using the modified cold start embeddings in the next iteration
    tmp_embeds = deepcopy(embeds)
    if transe_config["cold_start_embeddings"] == "avg":
        for user in users:
            nb_relations = 0
            for relation, entity in dataset.data_args.user_relation.items():
                # print('relation :', relation)
                # print('entity   :', entity)
                # entity[0] = entity_file.txt
                # entity[1] = entity_type
                # get all entities related to user by relation
                entities = getattr(dataset, relation, None)["data"][user]
                # get all related entities embeddings and subtract the relation embedding
                all_related_emb = (
                    embeds[entity[1]][entities] - embeds[relation][0]
                )
                nb_relations += all_related_emb.shape[0]
                # sum all related entities embeddings
                tmp_embeds["user"][user] += all_related_emb.sum(axis=0)
            # divide by the number of relations to get the average
            if nb_relations > 0:
                tmp_embeds["user"][user] /= nb_relations
                
    elif transe_config["cold_start_embeddings"] == "zero":
        for user in users:
            # set all cold start users embeddings to 0
            tmp_embeds["user"][user] = 0 
        
    elif transe_config["cold_start_embeddings"] == "posneg":
        for user in users:
            nb_relations = 0
            for relation, entity in dataset.data_args.user_relation.items():
                print('relation :', relation)
                print('entity   :', entity)
                # get all entities related to user by relation
                entities = getattr(dataset, relation, None)["data"][user]
                # get all related entities embeddings and subtract the relation embedding
                all_related_emb = (
                    embeds[entity[1]][entities] - embeds[relation][0]
                )
                # nb_relations += all_related_emb.shape[0]
                # sum all related entities embeddings
                if relation in ['interested_in', 'like']:
                    tmp_embeds["user"][user] += all_related_emb.sum(axis=0)
                elif relation in ['disinterested_in', 'dislike']:
                    tmp_embeds["user"][user] += all_related_emb.sum(axis=0)
            # divide by the number of relations to get the average
            if nb_relations > 0:
                tmp_embeds["user"][user] /= nb_relations
                
    return tmp_embeds

In [30]:
zero_embeds = {'user': np.zeros(100,)}
zero_embeds['user']

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])

In [31]:
# e_new = translation(
#     zero_embeds,    #zero embedding which is zero
#     new_dataset     #user preferred
# )

e_candidates = translation(
    embeds,         #past users embedding
    dataset         #past history
)

relation : mentioned
entity   : ['mentioned_by_u_w.txt', 'word']
relation : interested_in
entity   : ['interested_in_u_c.txt', 'category']
relation : like
entity   : ['like_u_b.txt', 'brand']
relation : mentioned
entity   : ['mentioned_by_u_w.txt', 'word']
relation : interested_in
entity   : ['interested_in_u_c.txt', 'category']
relation : like
entity   : ['like_u_b.txt', 'brand']
relation : mentioned
entity   : ['mentioned_by_u_w.txt', 'word']
relation : interested_in
entity   : ['interested_in_u_c.txt', 'category']
relation : like
entity   : ['like_u_b.txt', 'brand']
relation : mentioned
entity   : ['mentioned_by_u_w.txt', 'word']
relation : interested_in
entity   : ['interested_in_u_c.txt', 'category']
relation : like
entity   : ['like_u_b.txt', 'brand']
relation : mentioned
entity   : ['mentioned_by_u_w.txt', 'word']
relation : interested_in
entity   : ['interested_in_u_c.txt', 'category']
relation : like
entity   : ['like_u_b.txt', 'brand']
relation : mentioned
entity   : ['mentio

In [18]:
e_candidates['user']

array([[ 0.08093348, -0.1421791 , -0.06961356, ..., -0.18358433,
        -0.13157055,  0.10908696],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       ...,
       [-0.0126727 , -0.10156241,  0.00050613, ..., -0.15174106,
        -0.06665201,  0.0113936 ],
       [-0.03077982, -0.04668544, -0.00543377, ..., -0.10364935,
        -0.00625735,  0.00555829],
       [-0.00526187, -0.06766861, -0.01785942, ..., -0.11529686,
        -0.02912037,  0.02666572]], dtype=float32)

In [ ]:
dataset.data_args.user_relation.items()

## Cosine-Similarity

In [19]:
import numpy as np

def sim_function(e_new, e_candidates):
    # Compute norms
    norm_e_new = np.linalg.norm(e_new)
    norm_e_candidates = np.linalg.norm(e_candidates, axis=1)
    
    # Handle zero norms by setting them to a small positive value
    norm_e_new = norm_e_new if norm_e_new != 0 else 1e-9
    norm_e_candidates[norm_e_candidates == 0] = 1e-9
    
    # Compute cosine similarity
    cosine = np.dot(e_candidates, e_new) / (norm_e_candidates * norm_e_new)
    # Find the index of the maximum cosine similarity
    idx_cand = np.argmax(cosine)
    return cosine, idx_cand


In [20]:
cos_sim, idx_cand = sim_function(e_candidates['user'][0], e_candidates['user'])
cos_sim, idx_cand

(array([1.        , 0.        , 0.        , ..., 0.791132  , 0.36038256,
        0.71757424], dtype=float32),
 0)

In [23]:
e_candidates['user'][idx_cand]

array([ 0.08093348, -0.1421791 , -0.06961356,  0.11138001,  0.07570753,
        0.13874458,  0.13010576, -0.08096536, -0.13505611, -0.10520144,
        0.07965258, -0.08101346, -0.11111888, -0.1304944 , -0.05592651,
       -0.15060635,  0.13702847, -0.11917663,  0.08047727,  0.06196502,
        0.09108622, -0.04729382, -0.11556535, -0.08258695, -0.20351268,
        0.16212076,  0.10533641, -0.10644554, -0.14574294,  0.09326702,
        0.09700708, -0.0882481 ,  0.15235476,  0.16389291, -0.11206293,
        0.09716592,  0.07250672, -0.14501975,  0.15754525,  0.11278289,
       -0.0923283 , -0.11871436, -0.09719329, -0.09406462,  0.10433488,
       -0.11969016, -0.09527619,  0.08415918,  0.09386041,  0.0626181 ,
       -0.11769975, -0.15176436, -0.09028363, -0.13292195, -0.04932234,
        0.07949216, -0.12429279,  0.08291182, -0.08197957,  0.0982039 ,
       -0.08207585, -0.12176999, -0.08923937,  0.13884965, -0.16352499,
        0.12618157, -0.06468722, -0.10722491, -0.17409381,  0.13

## Trim